In [0]:
%run Workspace/team6_retail_sales_analysis/credentials

In [0]:
from pyspark.sql.functions import col, broadcast, lit
from time import time

#  Optimizations
spark.conf.set("spark.sql.adaptive.enabled", "true")
spark.conf.set("spark.sql.shuffle.partitions", "300")
spark.conf.set("spark.sql.autoBroadcastJoinThreshold", 50 * 1024 * 1024)
spark.conf.set("spark.databricks.delta.optimizeWrite.enabled", "true")
spark.conf.set("spark.databricks.delta.autoCompact.enabled", "true")

print("Spark optimizations applied.\n")



Spark optimizations applied.



### **Optimization -** Column Pruning, Repartitioning, Broadcasting, Cache, Coalesce

In [0]:
silver_path = "abfss://source@team6geocartdata.dfs.core.windows.net/geocartdata/staging/"

In [0]:

import time 
from pyspark.sql.functions import col, broadcast

# Load Staging Delta Tables

customers = spark.read.format("delta").load(
    silver_path + "customers/"
)
products = spark.read.format("delta").load(
    silver_path + "products/"
)

transactions = spark.read.format("delta").load(
    silver_path + "transactions/"
)

regions = spark.read.format("delta").load(
    silver_path + "regions/"
)

support = spark.read.format("delta").load(
    silver_path + "support_tickets/"
)

print("Loaded all Delta staging tables.\n")


customers_sel = customers.select(
    "CustomerID",
    "Gender", "Age", "JoinDate",
    col("City").alias("CustomerCity"),
    col("State").alias("CustomerState"),
    col("Country").alias("CustomerCountry"),
    "LoyaltyTier", "IsActive", col("RegionID").alias("CustomerRegionID")
)

products_sel = products.select(
    "ProductID", "ProductName", "Category", "SubCategory",
    "Brand", "Color", "Size", "Rating", "StockStatus"
)

transactions_sel = transactions.select(
    "TransactionID", "CustomerID", "ProductID", "RegionID",
    "TransactionDate", "Quantity", "UnitPrice", "DiscountPercent",
    "TaxAmount", "TotalAmount", "PaymentType", "Channel",
    "Status", "PromoCode", "ReturnFlag", "LineStatus",
    "Currency", "DeviceType"
)

regions_sel = regions.select(
    "RegionID", "RegionName", "SalesTarget", "TaxRate",
    "City", "State", "Country"
)

support_sel = support.select(
    "TicketID", "CustomerID", "IssueType", "Priority",
    col("Status").alias("TicketStatus"),
    "SLA_Breached", "ResolutionTimeMins",
    "SatisfactionRating", "SentimentScore",
    col("CreatedAt").alias("TicketCreatedAt")
)
print("Column pruning completed.\n")



# Logical Optimization (Repartitioning)

customers_df = customers_sel.repartition(8, "CustomerID")
transactions_df = transactions_sel.repartition(12, "CustomerID", "ProductID")
products_df = products_sel.repartition(4, "ProductID")
regions_df = regions_sel.repartition(2, "RegionID")
support_df = support_sel.repartition(6, "CustomerID")

print("Repartitioning applied for better parallelism.\n")

# Broadcast Joins 

# Join transactions → customers 
join1 = transactions_sel.join(broadcast(customers_df), "CustomerID", "inner")

# Join products
join2 = join1.join(broadcast(products_df), "ProductID", "inner")

# Join regions
join3 = join2.join(broadcast(regions_df), "RegionID", "inner")

# Join support tickets (LEFT JOIN)
final_df = join3.join(broadcast(support_df), "CustomerID", "left")

print("Broadcast joins completed.\n")

# Select Final GOLD Columns

final_df = final_df.select(
    "TransactionID", "CustomerID", "ProductID", "RegionID",
    "TransactionDate", "Quantity", "UnitPrice", "DiscountPercent",
    "TaxAmount", "TotalAmount", "PaymentType", "Channel",
    "Status", "PromoCode", "ReturnFlag", "LineStatus",
    "Currency", "DeviceType",

    # PRODUCT
    "ProductName", "Category", "SubCategory",
    "Brand", "Color", "Size", "Rating", "StockStatus",

    # CUSTOMER
    "Gender", "Age", "JoinDate",
    "CustomerCity", "CustomerState", "CustomerCountry",
    "LoyaltyTier", "IsActive",

    # REGION
    "RegionName", "SalesTarget", "TaxRate",

    # SUPPORT TICKETS
    "TicketID", "IssueType", "Priority", "TicketStatus",
    "SLA_Breached", "ResolutionTimeMins",
    "SatisfactionRating", "SentimentScore",
    "TicketCreatedAt"
)

print("Final GOLD columns selected.\n")

#Without Cache

print("Running validation query (without cache)...")
start_time = time.time()

optimized_result = (
    final_df
        .filter(col("CustomerID").isNotNull())
        .groupBy("TicketStatus")
        .count()
        .collect()
)

end_time = time.time()
print(f"Validation query executed in {round(end_time - start_time, 2)} seconds (no cache).\n")


# Cache Final DF for Performance

print("Caching final_df...")
final_df.cache()
final_df.count()
print("Cached final_df.\n")

# Query Performance Validation (With Cache)

print("Running validation query (with caching)...")
start_time = time.time()
optimized_result = final_df.filter(col("CustomerID").isNotNull()).groupBy("TicketStatus").count().collect()
end_time = time.time()
print(f"Validation query executed in {round(end_time - start_time, 2)} seconds (cached).\n")


#  Coalesce → Reduce small files

final_df = final_df.coalesce(4)
print("Coalesced to 4 files.\n")
print("GOLD LAYER PIPELINE COMPLETED SUCCESSFULLY ")


Loaded all Delta staging tables.

Column pruning completed.

Repartitioning applied for better parallelism.

Broadcast joins completed.

Final GOLD columns selected.

Running validation query (without cache)...
Validation query executed in 10.28 seconds (no cache).

Caching final_df...
Cached final_df.

Running validation query (with caching)...
Validation query executed in 1.72 seconds (cached).

Coalesced to 4 files.

GOLD LAYER PIPELINE COMPLETED SUCCESSFULLY 


In [0]:
from pyspark.sql.functions import year, month

# Adding year & month columns
final_df = final_df.withColumn("Year", year("TransactionDate")) \
                   .withColumn("Month", month("TransactionDate"))

# Then partition
gold_path = "abfss://source@team6geocartdata.dfs.core.windows.net/geocartdata/curated/join_retail_curated_data/"

final_df.write.format("delta") \
    .partitionBy("Year", "Month",) \
    .mode("overwrite") \
    .save(gold_path)
    
print("Data saved as Delta with Year/Month partitions.")



Data saved as Delta with Year/Month partitions.


## **Delta Table**

In [0]:
final_df.display(30)

TransactionID CustomerID ProductID RegionID TransactionDate Quantity UnitPrice DiscountPercent TaxAmount TotalAmount PaymentType Channel Status PromoCode ReturnFlag LineStatus Currency DeviceType ProductName Category SubCategory Brand Color Size Rating StockStatus Gender Age JoinDate CustomerCity CustomerState CustomerCountry LoyaltyTier IsActive RegionName SalesTarget TaxRate TicketID IssueType Priority TicketStatus SLA_Breached ResolutionTimeMins SatisfactionRating SentimentScore TicketCreatedAt Year Month 148 6915 5926 5192 2023-09-26 1.0 1113.85 5.0 200.49 1258.65 Net Banking Web Failed NEWUSER N O INR Desktop Pro Watch Home & Kitchen Kids Cartpro Blue XL 3.32 Low Stock Other 69 2025-06-06 Kolkata Karnataka Germany Platinum true Region-5192 1525249.9 0.131 2228 Damaged Product Low Resolved true 534.0 2.35 0.26 12-02-2025 2023 9 463 8202 3288 2629 2024-04-28 3.0 1604.97 0.0 866.68 5681.59 Net Banking In-store Refunded SAVE10 Y O GBP Tablet Pro Headphones Beauty Office Primeline Green XL 4.79 Out Of Stock Male 24 2024-06-16 Berlin West Bengal Uk Bronze true Region-2629 2741649.5 0.164 963 Damaged Product Medium Escalated false 61.0 3.34 0.0 15-06-2023 2024 4 496 2324 3862 2350 2025-02-22 4.0 1552.12 20.0 1117.53 6084.31 UPI Web Pending null N O USD Desktop Ultra Watch Grocery Outdoor Homesense Black L 4.93 Low Stock Male 40 2025-06-02 Dublin Île-de-france Canada Silver true Region-2350 1716286.6 0.083 6257 Late Delivery High Resolved true 7006.0 4.04 0.0 15-06-2023 2025 2 833 5779 5936 6320 2023-04-21 2.0 2198.22 20.0 791.36 4308.51 Net Banking In-store Failed null N O EUR Tablet Ultra Watch Beauty Premium Activex Black XS 3.78 Out Of Stock Female 73 2025-01-17 New York Delhi Ncr Usa Bronze true Region-6320 4315135.5 0.196 8797 Wrong Item Urgent Escalated false 8266.0 2.21 0.37 16-09-2023 2023 4 1088 7836 2147 9083 2024-09-22 1.0 1915.72 20.0 344.83 1877.41 Unknown Marketplace Completed FEST20 N O CAD Ios Max Headphones Beauty Budget Cartpro Grey S 4.73 In Stock Other 79 2023-04-13 London Delhi Ncr Uk Platinum true Region-9083 3145939.5 0.112 4737 Wrong Item Urgent Open false 3351.0 2.22 0.24 07-08-2023 2024 9 1342 1521 8544 7124 2023-08-04 5.0 1222.07 20.0 1099.86 5988.14 Credit Card Mobile Pending NEWUSER N F GBP Tablet Eco Shoes Electronics Kids Urbanedge Blue S 3.0 Out Of Stock Other 48 2023-08-21 Delhi Telangana Usa Platinum true Region-7124 4023028.8 0.128 2279 Wrong Item Medium Closed false 1237.0 2.18 0.0 18-03-2025 2023 8 1645 7606 6496 5249 2023-08-31 4.0 1250.12 15.0 900.09 5150.5 Net Banking In-store Refunded SAVE10 N F EUR Ios Ultra Shoes Fashion Premium Luxora Red XXL 4.9 In Stock Other 59 2024-02-09 Sydney Karnataka Australia Platinum true Region-5249 2983642.2 0.093 6456 Damaged Product High In Progress false 8166.0 4.21 0.8 23-03-2025 2023 8 1829 9810 3158 8583 2025-07-06 5.0 1528.57 0.0 1375.71 9018.56 COD Web Completed BOGO N O EUR Tablet Pro Headphones Grocery Premium Homesense Green XS 3.13 Low Stock Male 75 2023-12-16 Bengaluru Telangana Canada Silver true Region-8583 1237823.4 0.188 7880 Wrong Item Urgent Resolved false 1647.0 2.86 0.0 03-08-2023 2025 7 1959 497 8312 8466 2023-09-04 2.0 720.76 0.0 259.47 1700.99 Credit Card Web Refunded FEST20 N F GBP Ios Max Phone Home & Kitchen Standard Luxora Red XS null In Stock Female 28 2024-10-23 Hyderabad Telangana Usa Silver true Region-8466 4272285.5 0.072 8551 Damaged Product Medium Escalated true 2991.0 3.56 0.0 27-06-2025 2023 9 2142 8949 4019 950 2024-03-16 4.0 917.93 0.0 660.91 4332.63 Debit Card Web Completed null N F USD Desktop Lite Headphones Grocery Kids Urbanedge White M 3.91 Low Stock Other 40 2024-02-09 Dublin New York Uk Bronze true Region-950 4319566.0 0.093 4415 Late Delivery Low Open false 4726.0 3.49 0.29 07-05-2025 2024 3 2366 3989 1985 6010 2025-02-26 5.0 778.41 5.0 700.57 4398.02 Wallet Web Failed SAVE10 N O AUD Ios Ultra Phone Toys Outdoor Homesense Green XXL 4.3 Out Of Stock Female 76 2023-03-07 Sydney Delhi Ncr India Silver true Region